In [21]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import plotly_express as px
from scipy import stats as st
from scipy.stats import levene
from sklearn.metrics import make_scorer
from sklearn.model_selection import cross_val_score, GridSearchCV

from sklearn.linear_model import LinearRegression
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor



## 1.1

Importación de archivos


In [22]:

data_train = pd.read_csv("https://practicum-content.s3.us-west-1.amazonaws.com/datasets/gold_recovery_train.csv")
data_test = pd.read_csv("https://practicum-content.s3.us-west-1.amazonaws.com/datasets/gold_recovery_test.csv")
data_full = pd.read_csv("https://practicum-content.s3.us-west-1.amazonaws.com/datasets/gold_recovery_full.csv")

## 1.2

Comprueba que el calculo de recuperación sea correcto


In [23]:
#Columna con calculo de recuperación: data_train["rougher.output.recovery"]

# Función que calcula el % de recuperación
def recovery(df):
    c = df["rougher.output.concentrate_au"]
    f = df["rougher.input.feed_au"]
    t = df["rougher.output.tail_au"]
    try:
        result = ((c*(f-t))/(f*(c-t)))*100
    except:
        result = 0
    return result

recovery_calc = data_train.apply(lambda x: recovery(x), axis = 1)

print("Error absoluto medio del cálculo de recuperación:", (recovery_calc - data_train["rougher.output.recovery"]).abs().mean())

Error absoluto medio del cálculo de recuperación: 9.303415616264301e-15


Al tener un error absoluto medio tan bajo, podemos afirmar que los calculos han sido correctos hasta el momento


## 1.3

Analiza las características no disponibles del conjunto de prueba


In [24]:
not_in_test = set(data_train.columns) - set(data_test.columns)
not_in_test

{'final.output.concentrate_ag',
 'final.output.concentrate_au',
 'final.output.concentrate_pb',
 'final.output.concentrate_sol',
 'final.output.recovery',
 'final.output.tail_ag',
 'final.output.tail_au',
 'final.output.tail_pb',
 'final.output.tail_sol',
 'primary_cleaner.output.concentrate_ag',
 'primary_cleaner.output.concentrate_au',
 'primary_cleaner.output.concentrate_pb',
 'primary_cleaner.output.concentrate_sol',
 'primary_cleaner.output.tail_ag',
 'primary_cleaner.output.tail_au',
 'primary_cleaner.output.tail_pb',
 'primary_cleaner.output.tail_sol',
 'rougher.calculation.au_pb_ratio',
 'rougher.calculation.floatbank10_sulfate_to_au_feed',
 'rougher.calculation.floatbank11_sulfate_to_au_feed',
 'rougher.calculation.sulfate_to_au_concentrate',
 'rougher.output.concentrate_ag',
 'rougher.output.concentrate_au',
 'rougher.output.concentrate_pb',
 'rougher.output.concentrate_sol',
 'rougher.output.recovery',
 'rougher.output.tail_ag',
 'rougher.output.tail_au',
 'rougher.output.ta

Podemos observar que las columnas que no se encuentran en el conjunto de prueba son columnas tipo "output", valores que se obtienes después del procesado del material, es decir, valores futuros.


## 1.4

Preprocesamiento de datos


Para poder hacer un preprocesamiento adecuado, debemos tomar en cuenta 2 puntos importantes, el primero es que los datos cercanos en el tiempo suelen ser similares, y el segundo es que contamos con parámetros de fecha y hora para poder definir datos cercanos.


Buscamos la desviación estandar de 3 muestras de cada columna para corroborar que los datos realmente se acercan entre sí en fechas cercanas, (los datos en los df están ordenados por fecha y hora de registro)


In [25]:
for _ in range(3):
    rd = np.random.randint(0,22000)
    print(data_full.loc[rd:rd+5, :].drop(["date"], axis=1).std())

final.output.concentrate_ag                   0.306489
final.output.concentrate_pb                   0.148402
final.output.concentrate_sol                  0.406510
final.output.concentrate_au                   0.423059
final.output.recovery                         1.487220
                                                ...   
secondary_cleaner.state.floatbank5_a_level    2.003997
secondary_cleaner.state.floatbank5_b_air      0.008063
secondary_cleaner.state.floatbank5_b_level    0.211377
secondary_cleaner.state.floatbank6_a_air      0.008515
secondary_cleaner.state.floatbank6_a_level    0.311011
Length: 86, dtype: float64
final.output.concentrate_ag                   0.328970
final.output.concentrate_pb                   0.394475
final.output.concentrate_sol                  0.309279
final.output.concentrate_au                   1.169360
final.output.recovery                         6.255457
                                                ...   
secondary_cleaner.state.floatbank5_a_l

Al tener una desviación estandar normalmente no tan alejada en las columnas, sustituiremos los valores vacíos con los valores de el dato anterior más proximo en fecha


In [26]:
for data in [data_full,data_test,data_train]:
    data.ffill(inplace=True)
    data.isnull().sum()

## 2.1

Observa cómo cambia la concentracion de metales en función de cada etapa


In [27]:
columnas = pd.Series(data_full.columns)

au1 = data_full["rougher.input.feed_au"].mean()
au3 = data_full["rougher.output.concentrate_au"].mean()
au5 = data_full["primary_cleaner.output.concentrate_au"].mean()
au8 = data_full["final.output.concentrate_au"].mean()
oro = [au1, au3, au5, au8]

ag1 = data_full["rougher.input.feed_ag"].mean()
ag3 = data_full["rougher.output.concentrate_ag"].mean()
ag5 = data_full["primary_cleaner.output.concentrate_ag"].mean()
ag8 = data_full["final.output.concentrate_ag"].mean()
plata = [ag1, ag3, ag5, ag8]

pb1 = data_full["rougher.input.feed_pb"].mean()
pb3 = data_full["rougher.output.concentrate_pb"].mean()
pb5 = data_full["primary_cleaner.output.concentrate_pb"].mean()
pb8 = data_full["final.output.concentrate_pb"].mean()
plomo = [pb1, pb3, pb5, pb8]

stages = ['rougher_input', 'rougher_output', 'primary_cleaner', 'final_output']

fig = go.Figure(data=[
    go.Bar(name='Oro', x=stages, y=oro ),
    go.Bar(name='Plata', x=stages, y=plata),
    go.Bar(name='Plomo', x=stages, y=plomo)
])
# Change the bar mode
fig.update_layout(barmode='group', title_text = "Composición de la mezcla de metales en diferentes etapas")
fig.show()

Podemos ver un incremento constante de la cantidad de oro en la mezcla cuando las etapas son más avanzadas, mientras que la plata decrece despues de la salida rougher y el plomo llega a un punto máximo en primary cleaner


## 2.2

Compara las distribuciones del tamaño de las partículas de la alimentación en el conjunto de entrenamiento y en el conjunto de prueba.


In [28]:
train_particle_size = data_train["primary_cleaner.input.feed_size"]
test_particle_size = data_test["primary_cleaner.input.feed_size"]

print("diferencia de la media de ambas muestras: ", train_particle_size.mean() - test_particle_size.mean())

# Prueba de hipótesis
#H0: Los tamaños de partículas promedio para las muestras de entrenamiento y prueba son las mismas
#H1: Los tamaños de partículas promedio para las muestras de entrenamiento y prueba son diferentes
# levene = levene(train_particle_size, test_particle_size)
# if levene
tstudent_test = st.ttest_ind(train_particle_size,test_particle_size,equal_var=False)
print("p-value:",tstudent_test.pvalue)

fig = go.Figure()
fig.add_trace(go.Histogram(x=train_particle_size, name="Entrenamiento"))
fig.add_trace(go.Histogram(x=test_particle_size, name="Prueba"))

fig.update_layout(barmode='overlay')
fig.update_layout(xaxis=dict(range=[5, 10]))
fig.update_traces(opacity=0.75)
fig.show()

diferencia de la media de ambas muestras:  0.032633579011804414
p-value: 0.0004554672200801049


Aunque diferencia de la media de las distribuciones es insignificante en ambas muestras, al realizar la prueba de hipótesis para ambas muestras nuestro valor p nos muestra que existe suficiente evidencia como para afirmar que las distribuciones varían de la muestra de entrenamiento a la de prueba, es un punto a tomar en cuenta cuando entrenemos los modelos ya que podríamos tener problemas con los resultados al tener muestras no representativas de la población.


## 2.3

Considera las concentraciones totales de todas las sustancias en las diferentes etapas


In [29]:
#distribución de todas las partículas por etapa
materia_prima = data_full[["rougher.input.feed_ag","rougher.input.feed_pb","rougher.input.feed_sol", "rougher.input.feed_au"]]
concentrado_rougher = data_full[["rougher.output.concentrate_ag","rougher.output.concentrate_pb","rougher.output.concentrate_sol","rougher.output.concentrate_au"]]
concentrado_final = data_full[["final.output.concentrate_ag","final.output.concentrate_pb","final.output.concentrate_sol","final.output.concentrate_au"]]

name_of_stages = []
for stage in [materia_prima,concentrado_rougher,concentrado_final]:
    name_of_stages.extend(stage.columns)

def histo(etapa, titulo = ""):
    fig = go.Figure()
    fig.add_trace(go.Histogram(x=etapa.iloc[:,0], name="Plata"))
    fig.add_trace(go.Histogram(x=etapa.iloc[:,1], name="Plomo"))
    fig.add_trace(go.Histogram(x=etapa.iloc[:,2], name="Sol"))
    fig.add_trace(go.Histogram(x=etapa.iloc[:,3], name="Oro"))

    fig.update_layout(barmode='overlay', title_text= titulo)
    fig.update_traces(opacity=0.65, )
    return fig

histo(materia_prima, "Distribución de partículas en etapa de materia prima")

In [30]:
histo(concentrado_rougher, "Distribución de partículas en etapa de concentrado rougher" )

In [31]:
histo(concentrado_final,"Distribución de partículas en etapa de concentrado final" )

Observamos que hay muchos valores en el cuantil de 0, los excluiremos de nuestros datos ya que se podrían considerar anomalías


In [32]:
data_train = data_train.loc[(data_train != 0).any(axis=1)]
data_test = data_test.loc[(data_test != 0).any(axis=1)]


## 3.1

Escribe una función para calcular el valor final de sMAPE.


In [33]:
def sMAPE(obj, pred):
    N = len(obj)
    numerador = abs(obj - pred)
    denominador = (abs(obj) + abs(pred))/2
    return (sum(numerador/denominador)/N)*100

def final_sMAPE(y, y_pred):
    
    y_rougher = y.iloc[:,0]
    y_pred_rougher = y_pred[:,0]
    
    y_final = y.iloc[:,1]   
    y_pred_final = y_pred[:,1]
    
    smape_rougher = sMAPE(y_rougher, y_pred_rougher)
    smape_final = sMAPE(y_final, y_pred_final)
    
    return (0.25*smape_rougher + 0.75*smape_final)

## 3.2

Entrena diferentes modelos, utilizando la validación cruzada y la función sMAPE para evaluarlos


In [34]:
#Nombres de columnas para nuestros features y nuestros targets
features = data_test.columns.values
targets = ['rougher.output.recovery', 'final.output.recovery']

#Datos de entrenamiento
features_train = data_train[features].drop("date", axis=1)
target_train = data_train[targets]

#Datos de validación
#(Agregamos las columnas de target a nuestro dataset de test, ya que no se encuentran disponibles)
data_to_merge = data_full[['date','rougher.output.recovery', 'final.output.recovery']]

data_test = pd.merge(data_test, data_to_merge, on='date', how='left')

features_valid = data_test[features].drop("date", axis=1)
target_valid = data_test[targets]


In [35]:
#Llamamos a la función make_scorer para que scikitlearn acepte nuestro puntaje de sMAPE en una validación cruzada
sMAPE_score = make_scorer(final_sMAPE)

In [36]:
lr_model = LinearRegression()

# lr_scores = cross_val_score(lr_model, features_train, target_train, scoring = sMAPE_score, cv = 5)
# lr_final_score = lr_scores.mean()
# print('Puntajes sMAPE para cada iteración:', lr_scores)
# print('Modelo de Regresión Lineal | sMAPE = {:.6f}'.format(lr_final_score))


param_grid = {"fit_intercept": [True, False]}
grid_search = GridSearchCV(
    estimator=lr_model, param_grid=param_grid, scoring=sMAPE_score, cv=5
)
grid_search.fit(features_train, target_train)


best_params = grid_search.best_params_
best_model = grid_search.best_estimator_

predictions = best_model.predict(features_valid)
score = final_sMAPE(target_valid, predictions)

print("Mejores hiperparámetros:", best_params)
print("sMAPE:", score)

Mejores hiperparámetros: {'fit_intercept': True}
sMAPE: 12.311794657372834


In [37]:
def crear_modelo(modelo_elegido ):
    lr_model = modelo_elegido
    lr_scores = cross_val_score(lr_model, features_train, target_train, scoring = sMAPE_score, cv = 5)
    lr_final_score = lr_scores.mean()

    print('Puntajes sMAPE para cada iteración:', lr_scores)
    print(' | sMAPE = {:.6f}'.format(lr_final_score))

    # param_grid = grid_elegido
    # grid_search = GridSearchCV(estimator=lr_model, param_grid=param_grid, scoring=sMAPE_score, cv=5)
    # grid_search.fit(features_train, target_train)

    # best_params = grid_search.best_params_
    # best_model = grid_search.best_estimator_

    # predictions = best_model.predict(features_valid)
    # score = final_sMAPE(target_valid, predictions)

    # print("Mejores hiperparámetros:", best_params)
    # print("sMAPE:", score)
    # return predictions

In [38]:
# grid = {
#     'max_depth': [None, 5, 10, 15],
#     'min_samples_split': [2, 5, 10],
#     'min_samples_leaf': [1, 2, 4]
# }
crear_modelo(DecisionTreeRegressor())

# lr_model = DecisionTreeRegressor()
# # lr_scores = cross_val_score(lr_model, features_train, target_train, scoring = sMAPE_score, cv = 5)
# # lr_final_score = lr_scores.mean()

# # print('Puntajes sMAPE para cada iteración:', lr_scores)
# # print('Modelo de Regresión Lineal | sMAPE = {:.6f}'.format(lr_final_score))

# grid = {
#     'max_depth': [None, 5],
#     'min_samples_split': [2, 10],
#     'min_samples_leaf': [1, 4]
# }
# grid_search = GridSearchCV(estimator=lr_model, param_grid=grid, cv=5)
# grid_search.fit(features_train, target_train)

# best_params = grid_search.best_params_
# best_model = grid_search.best_estimator_

# predictions = best_model.predict(features_valid)
# score = final_sMAPE(target_valid, predictions)
# print(predictions)
# print("Mejores hiperparámetros:", best_params)
# print("sMAPE:", score)
# #Mejores hiperparámetros: {'max_depth': None, 'min_samples_leaf': 4, 'min_samples_split': 10}


Puntajes sMAPE para cada iteración: [        nan         nan         nan         nan 22.82586543]
 | sMAPE = nan


In [39]:
# grid = {
#     'n_estimators': [50, 100, 200],
#     'max_depth': [None, 10, 20],
#     'min_samples_split': [2, 5, 10],
#     'min_samples_leaf': [1, 2, 4]
# }
crear_modelo(RandomForestRegressor())

# lr_model = RandomForestRegressor()
# lr_scores = cross_val_score(lr_model, features_train, target_train, scoring = sMAPE_score, cv = 5)
# lr_final_score = lr_scores.mean()

# print('Puntajes sMAPE para cada iteración:', lr_scores)
# print('Modelo de Regresión Lineal | sMAPE = {:.6f}'.format(lr_final_score))

# grid = {
#     'n_estimators': [50, 100],
#     'max_depth': [None, 10]}
# grid_search = GridSearchCV(estimator=lr_model, param_grid=grid, cv=5)
# grid_search.fit(features_train, target_train)

# best_params = grid_search.best_params_
# best_model = grid_search.best_estimator_

# predictions = best_model.predict(features_valid)
# score = final_sMAPE(target_valid, predictions)
# print(predictions)
# print("Mejores hiperparámetros:", best_params)
# print("sMAPE:", score)

Puntajes sMAPE para cada iteración: [14.23099884 15.93794161 14.11567365 21.30981881 16.26394817]
 | sMAPE = 16.371676
